In [1]:
import pandas as pd
import numpy as np
from imblearn.over_sampling import RandomOverSampler
from sklearn.datasets import make_classification

from sklearn.model_selection import train_test_split

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


In [2]:
ml_dataframe_df = pd.read_csv("data/ml_dataframe.csv")


For the second model we increase the number of features used. This time we use
- tyre data 
- weather data (weather categories)
- grid position/ starting position
- position order -> final position of the drivers
- lap time
- pit stop time

For the tyre data, the lap times and the pit stop times we need to calculate rolling averages/ rolling medians of 

In [3]:
ml_dataframe_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2111 entries, 0 to 2110
Data columns (total 96 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   driverId                   2111 non-null   float64
 1   raceId                     2111 non-null   float64
 2   GP                         2111 non-null   object 
 3   year_x                     2111 non-null   int64  
 4   driverRef_x                2111 non-null   object 
 5   Full Wet                   2111 non-null   int64  
 6   Hard New                   2111 non-null   int64  
 7   Hard Used                  2111 non-null   int64  
 8   Hyper Soft                 2111 non-null   int64  
 9   Intermediate New           2111 non-null   int64  
 10  Intermediate Used          2111 non-null   int64  
 11  Medium New                 2111 non-null   int64  
 12  Medium Used                2111 non-null   int64  
 13  Soft New                   2111 non-null   int64

In [4]:

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

ml_dataframe_df.head(20)

driverId  raceId         GP  year_x driverRef_x  Full Wet  Hard New   
0        1.0   860.0  Australia    2012    hamilton         0         0  \
1        1.0   880.0  Australia    2013    hamilton         0         0   
2        1.0   926.0  Australia    2015    hamilton         0         0   
3        1.0   948.0  Australia    2016    hamilton         0         0   
4        1.0   969.0  Australia    2017    hamilton         0         0   
5        1.0   989.0  Australia    2018    hamilton         0         0   
6        1.0  1010.0  Australia    2019    hamilton         0         0   
7        1.0  1076.0  Australia    2022    hamilton         0        36   
8        1.0   861.0   Malaysia    2012    hamilton         0         0   
9        1.0   881.0   Malaysia    2013    hamilton         0        11   
10       1.0   901.0   Malaysia    2014    hamilton         0         5   
11       1.0   927.0   Malaysia    2015    hamilton         0        38   
12       1.0   963.0   Malaysia    2016    hamilton         0        20   
13       1.0   983.0   Malaysia    2017    hamilton         0         0   
14       1.0   863.0    Bahrain    2012    hamilton         0         0   
15       1.0   883.0    Bahrain    2013    hamilton         0        35   
16       1.0   902.0    Bahrain    2014    hamilton         0         0   
17       1.0   929.0    Bahrain    2015    hamilton         0         0   
18       1.0   949.0    Bahrain    2016    hamilton         0         0   
19       1.0   971.0    Bahrain    2017    hamilton         0         0   

    Hard Used  Hyper Soft  Intermediate New  Intermediate Used  Medium New   
0           0           0                 0                  0          41  \
1           0           0                 0                  0          45   
2           0           0                 0                  0          33   
3           0           0                 0                  0          41   
4           0           0                 0                  0           0   
5           0           0                 0                  0           0   
6           0           0                 0                  0          43   
7           0           0                 0                  0          22   
8           0           0                30                  0           0   
9           0           0                 7                  0          23   
10          0           0                 0                  0          51   
11          0           0                 0                  0          14   
12          0           0                 0                  0           0   
13          0           0                 0                  0           0   
14          0           0                 0                  0          35   
15          0           0                 0                  0           0   
16          0           0                 0                  0          16   
17          0           0                 0                  0          24   
18          0           0                 0                  0          15   
19          0           0                 0                  0           0   

    Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
0             0         0         17              0               0  \
1             0         0          0              0              13   
2             0         0         25              0               0   
3             0         0          0              0              16   
4             0        40          0              0               0   
5             0        39          0              0               0   
6             0         0         15              0               0   
7             0         0          0              0               0   
8            17         0          0              0               0   
9            15         0          0              0               0   
10      

In [5]:


columns_to_keep_merged = ['driverId','raceId', 'grid','positionOrder', 'Full Wet',
       'Hard New', 'Hard Used', 'Hyper Soft', 'Intermediate New',
       'Intermediate Used', 'Medium New', 'Medium Used', 'Soft New',
       'Soft Used', 'Supersoft New', 'Supersoft Used', 'Ultrasoft New',
       'Ultrasoft Used', 'Wet New', 'circuitId', 'weather_cloudy',
       'weather_cold', 'weather_dry', 'weather_warm', 'weather_wet', 'pit_stop_1_lap_x',
       'pit_stop_1_milliseconds_x', 'pit_stop_2_lap_x', 
        'pit_stop_2_milliseconds_x',
       'pit_stop_3_lap_x', 
       'pit_stop_3_milliseconds_x', 'pit_stop_4_lap_x',
       'pit_stop_4_milliseconds_x',
       'pit_stop_5_lap_x', 
       'pit_stop_5_milliseconds_x', 'pit_stop_6_lap_x',
       'pit_stop_6_milliseconds_x',  "date"  ]

new_merged_df = ml_dataframe_df[columns_to_keep_merged].copy()

print(new_merged_df)

      driverId  raceId  grid  positionOrder  Full Wet  Hard New  Hard Used   
0          1.0   860.0     1              3         0         0          0  \
1          1.0   880.0     3              5         0         0          0   
2          1.0   926.0     1              1         0         0          0   
3          1.0   948.0     1              2         0         0          0   
4          1.0   969.0     1              2         0         0          0   
5          1.0   989.0     1              2         0         0          0   
6          1.0  1010.0     1              2         0         0          0   
7          1.0  1076.0     5              4         0        36          0   
8          1.0   861.0     1              3         0         0          0   
9          1.0   881.0     4              3         0        11          0   
10         1.0   901.0     1              1         0         5          0   
11         1.0   927.0     1              2         0        38 

Convert the data to a time series

To be able to calculate the rolling averages we need to convert the date column toa time series.

In [6]:
new_merged_df['date'] = pd.to_datetime(new_merged_df['date'], format='%Y-%m-%d')
#new_merged_df.set_index('date', inplace=True)


In [7]:
new_merged_df['date'] = new_merged_df['date'].dt.date

In [23]:
query_result = new_merged_df[
    (new_merged_df['driverId'] == 842.0) &
    (new_merged_df['raceId'] == 1081) &
    (new_merged_df['circuitId'] == 73)
]

query_result

driverId  raceId  grid  positionOrder  Full Wet  Hard New  Hard Used   
1809     842.0  1081.0     6              5         0         0         42  \

      Hyper Soft  Intermediate New  Intermediate Used  Medium New   
1809           0                 0                  0           9  \

      Medium Used  Soft New  Soft Used  Supersoft New  Supersoft Used   
1809            0         0          0              0               0  \

      Ultrasoft New  Ultrasoft Used  Wet New  circuitId  weather_cloudy   
1809              0               0        0         73           False  \

      weather_cold  weather_dry  weather_warm  weather_wet  pit_stop_1_lap_x   
1809         False        False          True        False               9.0  \

      pit_stop_1_milliseconds_x  pit_stop_2_lap_x  pit_stop_2_milliseconds_x   
1809                    22698.0               0.0                        0.0  \

      pit_stop_3_lap_x  pit_stop_3_milliseconds_x  pit_stop_4_lap_x   
1809               0.0                        0.0               0.0  \

      pit_stop_4_milliseconds_x  pit_stop_5_lap_x  pit_stop_5_milliseconds_x   
1809                        0.0               0.0                        0.0  \

      pit_stop_6_lap_x  pit_stop_6_milliseconds_x        date  
1809               0.0                        0.0  2022-06-12

In [8]:
import pandas as pd

# Define your window size
window_size = 3

# Assuming you already have the DataFrame named new_merged_df

# Convert specified columns to float
columns_to_convert = [
       'pit_stop_1_milliseconds_x', 
        'pit_stop_2_milliseconds_x',
       'pit_stop_3_milliseconds_x', 'pit_stop_4_lap_x', 
       'pit_stop_4_milliseconds_x',
       'pit_stop_5_lap_x', 
       'pit_stop_5_milliseconds_x', 'pit_stop_6_lap_x',
        'pit_stop_6_milliseconds_x']

new_merged_df[columns_to_convert] = new_merged_df[columns_to_convert].astype(float)




In [9]:
X = new_merged_df.drop("target_column", axis=1)  # Features
y = new_merged_df["target_column"]  # Target variable


KeyError: "['target_column'] not found in axis"

In [ ]:


# Define your window size
window_size = 3

# Assuming you already have the DataFrame named new_merged_df

# Convert specified columns to float
selected_columns = ['Full Wet',
       'Hard New', 'Hard Used', 'Hyper Soft', 'Intermediate New',
       'Intermediate Used', 'Medium New', 'Medium Used', 'Soft New',
       'Soft Used', 'Supersoft New', 'Supersoft Used', 'Ultrasoft New',
       'Ultrasoft Used', 'Wet New', 'pit_stop_1_lap_x', 
       'pit_stop_1_milliseconds_x', 'pit_stop_2_lap_x', 
        'pit_stop_2_milliseconds_x',
       'pit_stop_3_lap_x', 
       'pit_stop_3_milliseconds_x', 'pit_stop_4_lap_x', 
        'pit_stop_4_milliseconds_x',
       'pit_stop_5_lap_x', 
       'pit_stop_5_milliseconds_x', 'pit_stop_6_lap_x', 
        'pit_stop_6_milliseconds_x']

new_merged_df[selected_columns] = new_merged_df[selected_columns].astype(float)

# Calculate the rolling median for each selected column
for column in selected_columns:
    new_merged_df[f'{column}_rolling_median'] = new_merged_df[column].rolling(window=window_size).median()

# Print the updated DataFrame
print(new_merged_df)


      driverId  raceId  grid  positionOrder  Full Wet  Hard New  Hard Used   
0          1.0   860.0     1              3       0.0       0.0        0.0  \
1          1.0   880.0     3              5       0.0       0.0        0.0   
2          1.0   926.0     1              1       0.0       0.0        0.0   
3          1.0   948.0     1              2       0.0       0.0        0.0   
4          1.0   969.0     1              2       0.0       0.0        0.0   
5          1.0   989.0     1              2       0.0       0.0        0.0   
6          1.0  1010.0     1              2       0.0       0.0        0.0   
7          1.0  1076.0     5              4       0.0      36.0        0.0   
8          1.0   861.0     1              3       0.0       0.0        0.0   
9          1.0   881.0     4              3       0.0      11.0        0.0   
10         1.0   901.0     1              1       0.0       5.0        0.0   
11         1.0   927.0     1              2       0.0      38.0 

In [ ]:

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
new_merged_df.head(20)

driverId  raceId  grid  positionOrder  Full Wet  Hard New  Hard Used   
0        1.0   860.0     1              3       0.0       0.0        0.0  \
1        1.0   880.0     3              5       0.0       0.0        0.0   
2        1.0   926.0     1              1       0.0       0.0        0.0   
3        1.0   948.0     1              2       0.0       0.0        0.0   
4        1.0   969.0     1              2       0.0       0.0        0.0   
5        1.0   989.0     1              2       0.0       0.0        0.0   
6        1.0  1010.0     1              2       0.0       0.0        0.0   
7        1.0  1076.0     5              4       0.0      36.0        0.0   
8        1.0   861.0     1              3       0.0       0.0        0.0   
9        1.0   881.0     4              3       0.0      11.0        0.0   
10       1.0   901.0     1              1       0.0       5.0        0.0   
11       1.0   927.0     1              2       0.0      38.0        0.0   
12       1.0   963.0     1             18       0.0      20.0        0.0   
13       1.0   983.0     1              2       0.0       0.0        0.0   
14       1.0   863.0     2              8       0.0       0.0        0.0   
15       1.0   883.0     9              5       0.0      35.0        0.0   
16       1.0   902.0     2              1       0.0       0.0        0.0   
17       1.0   929.0     1              1       0.0       0.0        0.0   
18       1.0   949.0     1              3       0.0       0.0        0.0   
19       1.0   971.0     2              2       0.0       0.0        0.0   

    Hyper Soft  Intermediate New  Intermediate Used  Medium New  Medium Used   
0          0.0               0.0                0.0        41.0          0.0  \
1          0.0               0.0                0.0        45.0          0.0   
2          0.0               0.0                0.0        33.0          0.0   
3          0.0               0.0                0.0        41.0          0.0   
4          0.0               0.0                0.0         0.0          0.0   
5          0.0               0.0                0.0         0.0          0.0   
6          0.0               0.0                0.0        43.0          0.0   
7          0.0               0.0                0.0        22.0          0.0   
8          0.0              30.0                0.0         0.0         17.0   
9          0.0               7.0                0.0        23.0         15.0   
10         0.0               0.0                0.0        51.0          0.0   
11         0.0               0.0                0.0        14.0          4.0   
12         0.0               0.0                0.0         0.0          0.0   
13         0.0               0.0                0.0         0.0          0.0   
14         0.0               0.0                0.0        35.0         13.0   
15         0.0               0.0                0.0         0.0         22.0   
16         0.0               0.0                0.0        16.0          0.0   
17         0.0               0.0                0.0        24.0          0.0   
18         0.0               0.0                0.0        15.0          0.0   
19         0.0               0.0                0.0         0.0          0.0   

    Soft New  Soft Used  Supersoft New  Supersoft Used  Ultrasoft New   
0        0.0       17.0            0.0             0.0            0.0  \
1        0.0        0.0            0.0            13.0            0.0   
2        0.0       25.0            0.0             0.0            0.0   
3        0.0        0.0            0.0            16.0            0.0   
4       40.0        0.0            0.0             0.0            0.0   
5       39.0        0.0            0.0             0.0            0.0   
6        0.0       15.0            0.0             0.0            0.0   
7        0.0        0.0            0.0             0.0            0.0   
8        0.0        0.0            0.0             0.0            0.0

In [ ]:
new_merged_df.isna().sum()

driverId                                    0
raceId                                      0
grid                                        0
positionOrder                               0
Full Wet                                    0
Hard New                                    0
Hard Used                                   0
Hyper Soft                                  0
Intermediate New                            0
Intermediate Used                           0
Medium New                                  0
Medium Used                                 0
Soft New                                    0
Soft Used                                   0
Supersoft New                               0
Supersoft Used                              0
Ultrasoft New                               0
Ultrasoft Used                              0
Wet New                                     0
circuitId                                   0
weather_cloudy                              0
weather_cold                      

In [ ]:
# Drop rows with NaN (missing) values
new_merged_df.dropna(axis=0, inplace=True)

In [ ]:
new_merged_df.describe()

driverId       raceId         grid  positionOrder     Full Wet   
count  2109.000000  2109.000000  2109.000000    2109.000000  2109.000000  \
mean    527.233760   971.778568    10.601707      10.193931     0.294452   
std     389.149898    70.203572     6.076186       5.712502     3.380106   
min       1.000000   860.000000     0.000000       1.000000     0.000000   
25%      18.000000   904.000000     5.000000       5.000000     0.000000   
50%     815.000000   971.000000    10.000000      10.000000     0.000000   
75%     832.000000  1028.000000    16.000000      15.000000     0.000000   
max     853.000000  1095.000000    24.000000      24.000000    49.000000   

          Hard New    Hard Used   Hyper Soft  Intermediate New   
count  2109.000000  2109.000000  2109.000000       2109.000000  \
mean     11.174964     0.735420     0.276908          1.619251   
std      16.602428     4.540372     2.422644          6.072274   
min     -20.000000     0.000000     0.000000          0.000000   
25%       0.000000     0.000000     0.000000          0.000000   
50%       0.000000     0.000000     0.000000          0.000000   
75%      24.000000     0.000000     0.000000          0.000000   
max      71.000000    57.000000    42.000000         44.000000   

       Intermediate Used   Medium New  Medium Used     Soft New    Soft Used   
count        2109.000000  2109.000000  2109.000000  2109.000000  2109.000000  \
mean            0.090564    13.779042     3.381223    11.092935     5.247037   
std             1.463941    16.823464     8.903752    15.816785    10.612332   
min             0.000000     0.000000     0.000000     0.000000     0.000000   
25%             0.000000     0.000000     0.000000     0.000000     0.000000   
50%             0.000000     0.000000     0.000000     0.000000     0.000000   
75%             0.000000    26.000000     0.000000    23.000000     0.000000   
max            33.000000    67.000000    51.000000    69.000000    51.000000   

       Supersoft New  Supersoft Used  Ultrasoft New  Ultrasoft Used   
count    2109.000000     2109.000000    2109.000000     2109.000000  \
mean        3.692271        2.978663       1.344239        1.123281   
std         9.908626        8.894118       6.762580        5.604448   
min         0.000000        0.000000       0.000000        0.000000   
25%         0.000000        0.000000       0.000000        0.000000   
50%         0.000000        0.000000       0.000000        0.000000   
75%         0.000000        0.000000       0.000000        0.000000   
max        64.000000       63.000000      75.000000       66.000000   

           Wet New    circuitId  pit_stop_1_lap_x  pit_stop_1_milliseconds_x   
count  2109.000000  2109.000000       2109.000000               2.109000e+03  \
mean      0.714083    29.434803         16.682314               5.971093e+04   
std       3.383504    28.282848         10.323173               2.044296e+05   
min       0.000000     1.000000          0.000000               0.000000e+00   
25%       0.000000     4.000000         10.000000               2.248200e+04   
50%       0.000000    18.000000         15.000000               2.433200e+04   
75%       0.000000    69.000000         24.000000               2.834700e+04   
max      31.000000    78.000000         64.000000               2.010361e+06   

       pit_stop_2_lap_x  pit_stop_2_milliseconds_x  pit_stop_3_lap_x   
count       2109.000000               2.109000e+03       2109.000000  \
mean          20.081555               5.823248e+04         10.948317   
std           17.800203               2.388326e+05         18.456130   
min            0.000000               0.000000e+00          0.000000   
25%            0.000000               0.000000e+00          0.000000   
50%           22.000000               2.226400e+04          0.000000   
75%           34.000000               2.491800e+04         25.000000   
max           74.000000               2.048175e+06         73.000000   


In [ ]:
# Calculate the rolling median
rolling_median = new_merged_df[selected_columns].rolling(window=window_size).median()

# Rename the columns by adding '_rolling_median' as a suffix
rolling_median.columns = [col + '_rolling_median' for col in selected_columns]

# Add the rolling median columns to the original DataFrame
new_merged_df_rolling = pd.concat([new_merged_df, rolling_median], axis=1)

# Display the updated DataFrame
#print(new_merged_df_rolling)
new_merged_df_rolling.to_csv("data/new_merged_df_rolling.csv")


Do tos:

- set the time frame to last 3 years
- filter the team first ()
-


In [ ]:
new_merged_df_rolling.head(10)

driverId  raceId  grid  positionOrder  Full Wet  Hard New  Hard Used   
2        1.0   926.0     1              1       0.0       0.0        0.0  \
3        1.0   948.0     1              2       0.0       0.0        0.0   
4        1.0   969.0     1              2       0.0       0.0        0.0   
5        1.0   989.0     1              2       0.0       0.0        0.0   
6        1.0  1010.0     1              2       0.0       0.0        0.0   
7        1.0  1076.0     5              4       0.0      36.0        0.0   
8        1.0   861.0     1              3       0.0       0.0        0.0   
9        1.0   881.0     4              3       0.0      11.0        0.0   
10       1.0   901.0     1              1       0.0       5.0        0.0   
11       1.0   927.0     1              2       0.0      38.0        0.0   

    Hyper Soft  Intermediate New  Intermediate Used  Medium New  Medium Used   
2          0.0               0.0                0.0        33.0          0.0  \
3          0.0               0.0                0.0        41.0          0.0   
4          0.0               0.0                0.0         0.0          0.0   
5          0.0               0.0                0.0         0.0          0.0   
6          0.0               0.0                0.0        43.0          0.0   
7          0.0               0.0                0.0        22.0          0.0   
8          0.0              30.0                0.0         0.0         17.0   
9          0.0               7.0                0.0        23.0         15.0   
10         0.0               0.0                0.0        51.0          0.0   
11         0.0               0.0                0.0        14.0          4.0   

    Soft New  Soft Used  Supersoft New  Supersoft Used  Ultrasoft New   
2        0.0       25.0            0.0             0.0            0.0  \
3        0.0        0.0            0.0            16.0            0.0   
4       40.0        0.0            0.0             0.0            0.0   
5       39.0        0.0            0.0             0.0            0.0   
6        0.0       15.0            0.0             0.0            0.0   
7        0.0        0.0            0.0             0.0            0.0   
8        0.0        0.0            0.0             0.0            0.0   
9        0.0        0.0            0.0             0.0            0.0   
10       0.0        0.0            0.0             0.0            0.0   
11       0.0        0.0            0.0             0.0            0.0   

    Ultrasoft Used  Wet New  circuitId  weather_cloudy  weather_cold   
2              0.0      0.0          1            True         False  \
3              0.0      0.0          1            True         False   
4             17.0      0.0          1            True         False   
5             19.0      0.0          1           False         False   
6              0.0      0.0          1           False         False   
7              0.0      0.0          1            True         False   
8              0.0      9.0          2           False         False   
9              0.0      0.0          2           False         False   
10             0.0      0.0          2           False         False   
11             0.0      0.0          2           False         False   

    weather_dry  weather_warm  weather_wet  pit_stop_1_lap_x   
2         False         False        False              25.0  \
3         False         False        False              16.0   
4         False         False        False              17.0   
5         False          True        False              19.0   
6         False          True        False              15.0   
7         False         False        False              22.0   
8         False          True        False               5.0   
9         False          True        False               7.0   
10         True         False        False              15.0   
11        False          True        False       

In [ ]:
new_merged_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 2109 entries, 2 to 2110
Data columns (total 65 columns):
 #   Column                                    Non-Null Count  Dtype  
---  ------                                    --------------  -----  
 0   driverId                                  2109 non-null   float64
 1   raceId                                    2109 non-null   float64
 2   grid                                      2109 non-null   int64  
 3   positionOrder                             2109 non-null   int64  
 4   Full Wet                                  2109 non-null   float64
 5   Hard New                                  2109 non-null   float64
 6   Hard Used                                 2109 non-null   float64
 7   Hyper Soft                                2109 non-null   float64
 8   Intermediate New                          2109 non-null   float64
 9   Intermediate Used                         2109 non-null   float64
 10  Medium New                               

In [ ]:
new_merged_df.head()

driverId  raceId  grid  positionOrder  Full Wet  Hard New  Hard Used   
2       1.0   926.0     1              1       0.0       0.0        0.0  \
3       1.0   948.0     1              2       0.0       0.0        0.0   
4       1.0   969.0     1              2       0.0       0.0        0.0   
5       1.0   989.0     1              2       0.0       0.0        0.0   
6       1.0  1010.0     1              2       0.0       0.0        0.0   

   Hyper Soft  Intermediate New  Intermediate Used  Medium New  Medium Used   
2         0.0               0.0                0.0        33.0          0.0  \
3         0.0               0.0                0.0        41.0          0.0   
4         0.0               0.0                0.0         0.0          0.0   
5         0.0               0.0                0.0         0.0          0.0   
6         0.0               0.0                0.0        43.0          0.0   

   Soft New  Soft Used  Supersoft New  Supersoft Used  Ultrasoft New   
2       0.0       25.0            0.0             0.0            0.0  \
3       0.0        0.0            0.0            16.0            0.0   
4      40.0        0.0            0.0             0.0            0.0   
5      39.0        0.0            0.0             0.0            0.0   
6       0.0       15.0            0.0             0.0            0.0   

   Ultrasoft Used  Wet New  circuitId  weather_cloudy  weather_cold   
2             0.0      0.0          1            True         False  \
3             0.0      0.0          1            True         False   
4            17.0      0.0          1            True         False   
5            19.0      0.0          1           False         False   
6             0.0      0.0          1           False         False   

   weather_dry  weather_warm  weather_wet  pit_stop_1_lap_x   
2        False         False        False              25.0  \
3        False         False        False              16.0   
4        False         False        False              17.0   
5        False          True        False              19.0   
6        False          True        False              15.0   

   pit_stop_1_milliseconds_x  pit_stop_2_lap_x  pit_stop_2_milliseconds_x   
2                    22295.0               0.0                        0.0  \
3                    21940.0              18.0                  1090087.0   
4                    21709.0               0.0                        0.0   
5                    21821.0               0.0                        0.0   
6                    21515.0               0.0                        0.0   

   pit_stop_3_lap_x  pit_stop_3_milliseconds_x  pit_stop_4_lap_x   
2               0.0                        0.0               0.0  \
3               0.0                        0.0               0.0   
4               0.0                        0.0               0.0   
5               0.0                        0.0               0.0   
6               0.0                        0.0               0.0   

   pit_stop_4_milliseconds_x  pit_stop_5_lap_x  pit_stop_5_milliseconds_x   
2                        0.0               0.0                        0.0  \
3                        0.0               0.0                        0.0   
4                        0.0               0.0                        0.0   
5                        0.0               0.0                        0.0   
6                        0.0               0.0                        0.0   

   pit_stop_6_lap_x  pit_stop_6_milliseconds_x        date   
2               0.0                        0.0  2015-03-15  \
3               0.0                        0.0  2016-03-20   
4               0.0                        0.0  2017-03-26   
5               0.0                        0.0  2018-03-25   
6               0.0                        0.0  2019-03-17   

   Full Wet_rolling_median  Hard New_rolling_median  Hard Used_rolling_median   
2                      0.0                      0

In [ ]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

new_merged_df.columns




Index(['driverId', 'raceId', 'grid', 'positionOrder', 'Full Wet', 'Hard New',
       'Hard Used', 'Hyper Soft', 'Intermediate New', 'Intermediate Used',
       'Medium New', 'Medium Used', 'Soft New', 'Soft Used', 'Supersoft New',
       'Supersoft Used', 'Ultrasoft New', 'Ultrasoft Used', 'Wet New',
       'circuitId', 'weather_cloudy', 'weather_cold', 'weather_dry',
       'weather_warm', 'weather_wet', 'pit_stop_1_lap_x',
       'pit_stop_1_milliseconds_x', 'pit_stop_2_lap_x',
       'pit_stop_2_milliseconds_x', 'pit_stop_3_lap_x',
       'pit_stop_3_milliseconds_x', 'pit_stop_4_lap_x',
       'pit_stop_4_milliseconds_x', 'pit_stop_5_lap_x',
       'pit_stop_5_milliseconds_x', 'pit_stop_6_lap_x',
       'pit_stop_6_milliseconds_x', 'date', 'Full Wet_rolling_median',
       'Hard New_rolling_median', 'Hard Used_rolling_median',
       'Hyper Soft_rolling_median', 'Intermediate New_rolling_median',
       'Intermediate Used_rolling_median', 'Medium New_rolling_median',
       'Medium 

In [ ]:
columns_new_rolling = ['driverId', 'raceId', 'grid', 'positionOrder', 'circuitId','weather_cloudy', 'weather_cold', 'weather_dry',
       'weather_warm', 'weather_wet','Full Wet_rolling_median',
       'Hard New_rolling_median', 'Hard Used_rolling_median',
       'Hyper Soft_rolling_median', 'Intermediate New_rolling_median',
       'Intermediate Used_rolling_median', 'Medium New_rolling_median',
       'Medium Used_rolling_median', 'Soft New_rolling_median',
       'Soft Used_rolling_median', 'Supersoft New_rolling_median',
       'Supersoft Used_rolling_median', 'Ultrasoft New_rolling_median',
       'Ultrasoft Used_rolling_median', 'Wet New_rolling_median',
       'pit_stop_1_lap_x_rolling_median',
       'pit_stop_1_milliseconds_x_rolling_median',
       'pit_stop_2_lap_x_rolling_median',
       'pit_stop_2_milliseconds_x_rolling_median',
       'pit_stop_3_lap_x_rolling_median',
       'pit_stop_3_milliseconds_x_rolling_median',
       'pit_stop_4_lap_x_rolling_median',
       'pit_stop_4_milliseconds_x_rolling_median',
       'pit_stop_5_lap_x_rolling_median',
       'pit_stop_5_milliseconds_x_rolling_median',
       'pit_stop_6_lap_x_rolling_median',
       'pit_stop_6_milliseconds_x_rolling_median']

new_rolling_df = new_merged_df[columns_new_rolling].copy()

print(new_rolling_df)


      driverId  raceId  grid  positionOrder  circuitId  weather_cloudy   
2          1.0   926.0     1              1          1            True  \
3          1.0   948.0     1              2          1            True   
4          1.0   969.0     1              2          1            True   
5          1.0   989.0     1              2          1           False   
6          1.0  1010.0     1              2          1           False   
7          1.0  1076.0     5              4          1            True   
8          1.0   861.0     1              3          2           False   
9          1.0   881.0     4              3          2           False   
10         1.0   901.0     1              1          2           False   
11         1.0   927.0     1              2          2           False   
12         1.0   963.0     1             18          2           False   
13         1.0   983.0     1              2          2            True   
14         1.0   863.0     2          

In [ ]:
new_rolling_df.head()

driverId  raceId  grid  positionOrder  circuitId  weather_cloudy   
2       1.0   926.0     1              1          1            True  \
3       1.0   948.0     1              2          1            True   
4       1.0   969.0     1              2          1            True   
5       1.0   989.0     1              2          1           False   
6       1.0  1010.0     1              2          1           False   

   weather_cold  weather_dry  weather_warm  weather_wet   
2         False        False         False        False  \
3         False        False         False        False   
4         False        False         False        False   
5         False        False          True        False   
6         False        False          True        False   

   Full Wet_rolling_median  Hard New_rolling_median  Hard Used_rolling_median   
2                      0.0                      0.0                       0.0  \
3                      0.0                      0.0                       0.0   
4                      0.0                      0.0                       0.0   
5                      0.0                      0.0                       0.0   
6                      0.0                      0.0                       0.0   

   Hyper Soft_rolling_median  Intermediate New_rolling_median   
2                        0.0                              0.0  \
3                        0.0                              0.0   
4                        0.0                              0.0   
5                        0.0                              0.0   
6                        0.0                              0.0   

   Intermediate Used_rolling_median  Medium New_rolling_median   
2                               0.0                       41.0  \
3                               0.0                       41.0   
4                               0.0                       33.0   
5                               0.0                        0.0   
6                               0.0                        0.0   

   Medium Used_rolling_median  Soft New_rolling_median   
2                         0.0                      0.0  \
3                         0.0                      0.0   
4                         0.0                      0.0   
5                         0.0                     39.0   
6                         0.0                     39.0   

   Soft Used_rolling_median  Supersoft New_rolling_median   
2                      17.0                           0.0  \
3                       0.0                           0.0   
4                       0.0                           0.0   
5                       0.0                           0.0   
6                       0.0                           0.0   

   Supersoft Used_rolling_median  Ultrasoft New_rolling_median   
2                            0.0                           0.0  \
3                           13.0                           0.0   
4                            0.0                           0.0   
5                            0.0                           0.0   
6                            0.0                           0.0   

   Ultrasoft Used_rolling_median  Wet New_rolling_median   
2                            0.0                     0.0  \
3                            0.0                     0.0   
4                            0.0                     0.0   
5                           17.0                     0.0   
6                           17.0                     0.0   

   pit_stop_1_lap_x_rolling_median  pit_stop_1_milliseconds_x_rolling_median   
2                             17.0                                   22295.0  \
3                             16.0                                   22155.0   
4                             17.0                                   21940.0   
5                             17.0                                   21821.0   
6                             17.0                                   217

#### Oversampling

- Separate the features (X) and the target variable (y). In your case, it seems like you want to oversample based on some specific columns (e.g., 'positionOrder'):

In [ ]:
# Assuming 'positionOrder' is your target variable, and you want to oversample based on it
X = new_rolling_df.drop('positionOrder', axis=1)  # Features
y = new_rolling_df['positionOrder']  # Target variable


- Split dataset into training and testing subsets:


In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


- Create an instance of the RandomOverSampler:


In [ ]:
oversampler = RandomOverSampler(random_state=42)


- Use the oversampler to fit and transform your training data to oversample the minority class:


In [ ]:
X_train_resampled, y_train_resampled = oversampler.fit_resample(X_train, y_train)


In [ ]:
# Combine the oversampled training features and target variable into a new DataFrame
oversampled_train_df = pd.DataFrame(X_train_resampled, columns=X.columns)
oversampled_train_df['positionOrder'] = y_train_resampled


In [ ]:
oversampled_train_df.head()

driverId  raceId  grid  circuitId  weather_cloudy  weather_cold   
0       3.0   967.0     2         18           False         False  \
1     845.0   994.0    13          6           False         False   
2     831.0   963.0    18          2           False         False   
3     846.0  1017.0     5         34           False         False   
4      18.0   902.0     6          3           False         False   

   weather_dry  weather_warm  weather_wet  Full Wet_rolling_median   
0        False         False         True                      0.0  \
1        False          True        False                      0.0   
2        False          True        False                      0.0   
3        False          True        False                      0.0   
4         True         False        False                      0.0   

   Hard New_rolling_median  Hard Used_rolling_median   
0                      0.0                       0.0  \
1                      0.0                       0.0   
2                     14.0                       0.0   
3                     34.0                       0.0   
4                      0.0                       0.0   

   Hyper Soft_rolling_median  Intermediate New_rolling_median   
0                        0.0                              0.0  \
1                        0.0                              0.0   
2                        0.0                              0.0   
3                        0.0                              0.0   
4                        0.0                              0.0   

   Intermediate Used_rolling_median  Medium New_rolling_median   
0                               0.0                       19.0  \
1                               0.0                       18.0   
2                               0.0                       32.0   
3                               0.0                        0.0   
4                               0.0                       20.0   

   Medium Used_rolling_median  Soft New_rolling_median   
0                         0.0                      0.0  \
1                         0.0                      1.0   
2                         0.0                      0.0   
3                         0.0                      0.0   
4                        11.0                      0.0   

   Soft Used_rolling_median  Supersoft New_rolling_median   
0                       7.0                           0.0  \
1                       0.0                          16.0   
2                       0.0                           0.0   
3                       0.0                           0.0   
4                      10.0                           0.0   

   Supersoft Used_rolling_median  Ultrasoft New_rolling_median   
0                            0.0                           0.0  \
1                            0.0                           0.0   
2                            0.0                           0.0   
3                            0.0                           0.0   
4                            0.0                           0.0   

   Ultrasoft Used_rolling_median  Wet New_rolling_median   
0                            0.0                     0.0  \
1                            0.0                     0.0   
2                            0.0                     0.0   
3                            0.0                     0.0   
4                            0.0                     0.0   

   pit_stop_1_lap_x_rolling_median  pit_stop_1_milliseconds_x_rolling_median   
0                             13.0                                   25039.0  \
1                              7.0                                   24672.0   
2                             10.0                                   24697.0   
3                             18.0                                   21443.0   
4                              9.0                                   23093.0   

   pit_stop_2_lap_x_rolling_median  pit_stop_2_milliseconds_x_rolling_median   
0